In [81]:
import csv
from urllib.request import urlopen
import psycopg2
from psycopg2.extensions import ISOLATION_LEVEL_AUTOCOMMIT 
import pandas as pd
import io
import requests
from datetime import datetime, timedelta
import time
from datetime import date

In [82]:
## *****NOTE -
## *****This Needs to be Executed only once of the COVID_19, if DB is not present/ postgres is freshly installed.

# Connecting to default "postgres" database and using it we create covid_19 database
db_connection = psycopg2.connect(host='127.0.0.1',dbname="postgres", user="postgres" , password="root")

db_connection.set_isolation_level(ISOLATION_LEVEL_AUTOCOMMIT) 

cursor = db_connection.cursor()

# Creating "covid_19" database
#cursor.execute("CREATE DATABASE covid_19;")



In [83]:
#Once the covdid 19 DB is created we connect to "covid_19"

db_connection = psycopg2.connect(host='127.0.0.1',dbname="covid_19", user="postgres" , password="root")

cursor = db_connection.cursor()

db_connection.commit()

In [88]:
cursor.execute("DROP TABLE IF EXISTS covid_daily_report")
cursor.execute("DROP TABLE IF EXISTS covid_daily_report_us")
cursor.execute("DROP TABLE IF EXISTS covid_timeseries_report")

In [89]:
db_connection.commit()

In [90]:
 #cursor.execute("""CREATE TABLE covid_daily_report(
 #               province_state TEXT,
 #               country_region TEXT,
 #               last_updated timestamp,
 #               confirmed INTEGER,
 #               deaths INTEGER,
 #               recovered INTEGER,
 #               latitude FLOAT,
 #               longitude FLOAT);""")

    
cursor.execute("""CREATE TABLE covid_daily_report(
                FIPS TEXT,
                Admin2 TEXT,
                Province_State TEXT,
                Country_Region TEXT,
                Last_Update timestamp,
                Lat FLOAT,
                Long_ FLOAT,
                Confirmed INTEGER,
                Deaths INTEGER,
                Recovered INTEGER,
                Active INTEGER,
                Combined_Key TEXT);""")

#cursor.execute("""CREATE TABLE covid_daily_report_us(
#                province_state TEXT,
#                country_region TEXT,
#                last_updated TEXT,
#                confirmed INTEGER,
#                deaths INTEGER,
#                recovered INTEGER,
#                active INTEGER,
#                people_tested INTEGER,
#                people_hospitalized INTEGER,
#                latitude FLOAT,
#                longitude FLOAT);""")

cursor.execute("""CREATE TABLE covid_daily_report_us(
                Province_State TEXT,
                Country_Region TEXT,
                Last_Update TEXT,
                Lat FLOAT,
                Long_ FLOAT,
                Confirmed INTEGER,
                Deaths INTEGER,
                Recovered INTEGER,
                Active INTEGER,
                FIPS TEXT,
                Incident_Rate FLOAT,
                people_tested INTEGER,
                people_hospitalized INTEGER,
                Mortality_Rate FLOAT,
                UID TEXT,
                ISO3 TEXT,
                Testing_Rate FLOAT,
                Hospitalization_Rate FLOAT);""")

#cursor.execute("""CREATE TABLE covid_timeseries_report(
#                province_state TEXT,
#                country_region TEXT,
#                latitude FLOAT,
#                longitude FLOAT,
#                report_date TEXT,
#                total INTEGER,
#                category TEXT);""")

cursor.execute("""CREATE TABLE covid_timeseries_report(
                province_state TEXT,
                country_region TEXT,
                latitude FLOAT,
                longitude FLOAT,
                report_date TEXT,
                total INTEGER,
                category TEXT);""")

In [91]:
db_connection.commit()

In [43]:
    #**************** Start of Fetching Daily Report *********************#
    utc_datetime = datetime.utcnow()-timedelta(days=1)
    dt = utc_datetime.strftime("%m-%d-%Y")
    
    print("Pulling data from server - Daily Report")
    url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/"+dt+".csv"
    s=requests.get(url).content
    df=pd.read_csv(io.StringIO(s.decode('utf-8')))
    #df = df.rename(columns={
    #    "Province_State": "province_state",
    #    "Country_Region": "country_region",
    #    "Last_Update": "last_updated",
    #    "Confirmed": "confirmed",
    #    "Deaths": "deaths",
    #    "Recovered": "recovered",
    #    "Lat": "latitude",
    #    "Long_": "longitude"
    #})
    #df.drop(columns=['FIPS', 'Admin2', 'Active', 'Combined_Key'])
    df = df.fillna('')
    df.to_csv('covid_19_report_'+dt+'.csv',sep=',', encoding='utf-8', index=False)
    
    # delete existing data in the table
    cursor.execute("DELETE FROM covid_daily_report")
    # Saving the changes
    db_connection.commit()
    
    print("Started inserting data to DB - Daily Report")
    # Inserting each row
    for row in df.iterrows():
        fips = row[1]['FIPS']
        admin2 = row[1]['Admin2']
        province_state = row[1]['Province_State']
        country_region = row[1]['Country_Region']
        last_updated = row[1]['Last_Update']
        latitude = row[1]['Lat']
        longitude = row[1]['Long_']
        confirmed = row[1]['Confirmed']
        deaths = row[1]['Deaths']
        recovered = row[1]['Recovered']
        active = row[1]['Active']
        combined_key = row[1]['Combined_Key']

        # Incase the 's is present in the string it adds an escape character i.e. ''
        if(admin2 != ''):
            admin2 = admin2.replace("'","''")
        if(province_state != ''):
            province_state = province_state.replace("'","''")
        if(country_region != ''):
            country_region = country_region.replace("'","''")
        if(latitude == ''):
            latitude = 0.0
        if(longitude == ''):
            longitude = 0.0
        if(combined_key != ''):
            combined_key = combined_key.replace("'","''")
        

        query = """
        INSERT into covid_daily_report 
        values('%s','%s','%s','%s',TIMESTAMP '%s',
                %s,%s,%s,%s,%s,%s, '%s');
        """ % (fips, admin2, province_state, country_region, datetime.fromisoformat(last_updated),
              latitude, longitude, confirmed, deaths, recovered, active, combined_key)
        #print(query)
        cursor.execute(query)
    
    print("Ended inserting data to DB - Daily Report")
    # Close the connection - Saving the changes
    db_connection.commit()
    
    #**************** End of Fetching Daily Report *********************#

Pulling data from server - Daily Report
Started inserting data to DB - Daily Report
Ended inserting data to DB - Daily Report


In [68]:
    
    
    #**************** Start of Fetching US Daily Report *********************#
    utc_datetime = datetime.utcnow()-timedelta(days=1)
    dt = utc_datetime.strftime("%m-%d-%Y")

    print("Pulling data from server - US Daily Report")
    url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports_us/"+dt+".csv"
    s=requests.get(url).content
    df=pd.read_csv(io.StringIO(s.decode('utf-8')))
    df = df.fillna('')
    df.to_csv('covid_19_report_us_'+dt+'.csv',sep=',', encoding='utf-8', index=False)

    # delete existing data in the table
    cursor.execute("DELETE FROM covid_daily_report_us")
    # Saving the changes
    db_connection.commit()

    print("Started inserting data to DB - US Daily Report")
    # Inserting each row
    for row in df.iterrows():
        province_state = row[1]['Province_State']
        country_region = row[1]['Country_Region']
        last_updated = row[1]['Last_Update']
        latitude = row[1]['Lat']
        longitude = row[1]['Long_']
        confirmed = row[1]['Confirmed']
        deaths = row[1]['Deaths']
        recovered = row[1]['Recovered']
        active = row[1]['Active']
        fips = row[1]['FIPS']
        incident_rate  = row[1]['Incident_Rate']
        people_tested = row[1]['People_Tested']
        people_hospitalized = row[1]['People_Hospitalized']
        mortality_rate  = row[1]['Mortality_Rate']
        uid  = row[1]['UID']
        iso3  = row[1]['ISO3']
        testing_rate  = row[1]['Testing_Rate']
        hospitalization_rate  = row[1]['Hospitalization_Rate']

        # Incase the 's is present in the string it adds an escape character i.e. ''
        if(province_state != ''):
            province_state = province_state.replace("'","''")
        if(country_region != ''):
            country_region = country_region.replace("'","''")
        if(latitude == ''):
            latitude = 0.0
        if(longitude == ''):
            longitude = 0.0
        if(confirmed == ''):
            confirmed = 0
        if(deaths == ''):
            deaths = 0
        if(recovered == ''):
            recovered = 0
        if(active == ''):
            active = 0
        if(fips == ''):
            fips = ''
        if(people_tested == ''):
            people_tested = 0
        if(people_hospitalized == ''):
            people_hospitalized = 0
        if(incident_rate == ''):
            incident_rate = 0.0
        if(mortality_rate == ''):
            mortality_rate = 0.0
        if(uid == ''):
            uid = 0
        if(iso3 == ''):
            iso3 = 0
        if(testing_rate == ''):
            testing_rate = 0.0
        if(hospitalization_rate == ''):
            hospitalization_rate = 0.0



        query = """
        INSERT into covid_daily_report_us
        values('%s','%s','%s',%s,%s,
                %s,%s,%s,%s,'%s',
                %s,%s,%s,%s,'%s',
                '%s',%s,%s);
        """ % (province_state, country_region,last_updated,latitude, longitude,
              confirmed, deaths, recovered,active,fips,
              incident_rate, people_tested,people_hospitalized,mortality_rate, uid,
              iso3, testing_rate, hospitalization_rate)
        #print(query)
        cursor.execute(query)

    print("Ended inserting data to DB - US Daily Report")
    # Close the connection - Saving the changes
    db_connection.commit()

    #**************** End of Fetching US Daily Report *********************#
    

Pulling data from server - US Daily Report
Started inserting data to DB - US Daily Report
Ended inserting data to DB - US Daily Report


In [79]:
    
    #**************** Start of Fetching Timeseries Report *********************#
    
     # delete existing data in the table
    cursor.execute("DELETE FROM covid_timeseries_report")
    # Saving the changes
    db_connection.commit()
    category = ['confirmed','deaths','recovered']
    for cat in category:
        print("Pulling data from server - " + cat)
            #"https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv
        url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_"+cat+"_global.csv"
        print(url)
        s=requests.get(url).content
        df_conf=pd.read_csv(io.StringIO(s.decode('utf-8')))
        df_conf = df_conf.rename(columns={
            "Province/State": "province_state",
            "Country/Region": "country_region",
            "Lat": "latitude",
            "Long": "longitude"
        })
        df_conf = df_conf.fillna('')
        
        df_conf.to_csv('time_series_19-covid-'+cat+'.csv',sep=',', encoding='utf-8', index=False)
        
        # Getting all the dates as list
        dates_col = df_conf.columns[4:len(df_conf.columns)]

        df_datewise= df_conf[['province_state', 'country_region', 'latitude', 'longitude']].copy()

        print("Started inserting data to DB - " + cat)
        for d in dates_col:
            lst_count = list(df_conf[[d][0]])
            lst_same_date = [list(df_conf[[d]])[0] for i in range(len(lst_count))]
            lst_data_type = [cat for i in range(len(lst_count))]
            df_datewise['report_date'] = lst_same_date
            df_datewise['total'] = lst_count
            df_datewise['category'] = lst_data_type

            # Inserting data to database datewise 
            # Inserting each row
            for row in df_datewise.iterrows():
                print(row[1])
                province_state = row[1]['province_state']
                country_region = row[1]['country_region']

                # Incase the 's is present in the string it adds an escape character i.e. ''
                if(province_state != ''):
                    province_state = province_state.replace("'","''")
                if(country_region != ''):
                    country_region = country_region.replace("'","''")

                query = """
                INSERT into covid_timeseries_report(province_state, 
                    country_region, latitude, longitude,
                    report_date, total, category) 
                values('%s','%s',%s,%s,'%s',%s,'%s');
                """ % (province_state, country_region,
                       row[1]['latitude'], row[1]['longitude'],
                      row[1]['report_date'], row[1]['total'], row[1]['category'])
                cursor.execute(query)
        print("Ended inserting data to DB - " + cat)

        db_connection.commit()
    
    #**************** End of Fetching Timeseries Report *********************#

Pulling data from server - confirmed
https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv
Started inserting data to DB - confirmed
province_state               
country_region    Afghanistan
latitude                   33
longitude                  65
report_date           1/22/20
total                       0
category            confirmed
Name: 0, dtype: object
province_state             
country_region      Albania
latitude            41.1533
longitude           20.1683
report_date         1/22/20
total                     0
category          confirmed
Name: 1, dtype: object
province_state             
country_region      Algeria
latitude            28.0339
longitude            1.6596
report_date         1/22/20
total                     0
category          confirmed
Name: 2, dtype: object
province_state             
country_region      Andorra
latitude            42.5063
longitude       

province_state             
country_region     Slovenia
latitude            46.1512
longitude           14.9955
report_date         1/22/20
total                     0
category          confirmed
Name: 198, dtype: object
province_state             
country_region      Somalia
latitude             5.1521
longitude           46.1996
report_date         1/22/20
total                     0
category          confirmed
Name: 199, dtype: object
province_state                
country_region    South Africa
latitude              -30.5595
longitude              22.9375
report_date            1/22/20
total                        0
category             confirmed
Name: 200, dtype: object
province_state             
country_region        Spain
latitude                 40
longitude                -4
report_date         1/22/20
total                     0
category          confirmed
Name: 201, dtype: object
province_state             
country_region    Sri Lanka
latitude                  7
longitude  

province_state               
country_region    Afghanistan
latitude                   33
longitude                  65
report_date           1/23/20
total                       0
category            confirmed
Name: 0, dtype: object
province_state             
country_region      Albania
latitude            41.1533
longitude           20.1683
report_date         1/23/20
total                     0
category          confirmed
Name: 1, dtype: object
province_state             
country_region      Algeria
latitude            28.0339
longitude            1.6596
report_date         1/23/20
total                     0
category          confirmed
Name: 2, dtype: object
province_state             
country_region      Andorra
latitude            42.5063
longitude            1.5218
report_date         1/23/20
total                     0
category          confirmed
Name: 3, dtype: object
province_state             
country_region       Angola
latitude           -11.2027
longitude           17.873

Name: 160, dtype: object
province_state             
country_region     Mongolia
latitude            46.8625
longitude           103.847
report_date         1/23/20
total                     0
category          confirmed
Name: 161, dtype: object
province_state              
country_region    Montenegro
latitude                42.5
longitude               19.3
report_date          1/23/20
total                      0
category           confirmed
Name: 162, dtype: object
province_state             
country_region      Morocco
latitude            31.7917
longitude           -7.0926
report_date         1/23/20
total                     0
category          confirmed
Name: 163, dtype: object
province_state             
country_region      Namibia
latitude           -22.9576
longitude           18.4904
report_date         1/23/20
total                     0
category          confirmed
Name: 164, dtype: object
province_state             
country_region        Nepal
latitude            28.1667


province_state               
country_region    Afghanistan
latitude                   33
longitude                  65
report_date           1/24/20
total                       0
category            confirmed
Name: 0, dtype: object
province_state             
country_region      Albania
latitude            41.1533
longitude           20.1683
report_date         1/24/20
total                     0
category          confirmed
Name: 1, dtype: object
province_state             
country_region      Algeria
latitude            28.0339
longitude            1.6596
report_date         1/24/20
total                     0
category          confirmed
Name: 2, dtype: object
province_state             
country_region      Andorra
latitude            42.5063
longitude            1.5218
report_date         1/24/20
total                     0
category          confirmed
Name: 3, dtype: object
province_state             
country_region       Angola
latitude           -11.2027
longitude           17.873

...

province_state              
country_region    San Marino
latitude             43.9424
longitude            12.4578
report_date          4/12/20
total                    356
category           confirmed
Name: 191, dtype: object
province_state                
country_region    Saudi Arabia
latitude                    24
longitude                   45
report_date            4/12/20
total                     4462
category             confirmed
Name: 192, dtype: object
province_state             
country_region      Senegal
latitude            14.4974
longitude          -14.4524
report_date         4/12/20
total                   280
category          confirmed
Name: 193, dtype: object
province_state             
country_region       Serbia
latitude            44.0165
longitude           21.0059
report_date         4/12/20
total                  3630
category          confirmed
Name: 194, dtype: object
province_state              
country_region    Seychelles
latitude             -4.6796
l

province_state               
country_region    Afghanistan
latitude                   33
longitude                  65
report_date           4/13/20
total                     665
category            confirmed
Name: 0, dtype: object
province_state             
country_region      Albania
latitude            41.1533
longitude           20.1683
report_date         4/13/20
total                   467
category          confirmed
Name: 1, dtype: object
province_state             
country_region      Algeria
latitude            28.0339
longitude            1.6596
report_date         4/13/20
total                  1983
category          confirmed
Name: 2, dtype: object
province_state             
country_region      Andorra
latitude            42.5063
longitude            1.5218
report_date         4/13/20
total                   646
category          confirmed
Name: 3, dtype: object
province_state             
country_region       Angola
latitude           -11.2027
longitude           17.873

province_state             
country_region           US
latitude            37.0902
longitude          -95.7129
report_date         4/13/20
total                580619
category          confirmed
Name: 225, dtype: object
province_state              
country_region    Uzbekistan
latitude             41.3775
longitude            64.5853
report_date          4/13/20
total                    998
category           confirmed
Name: 226, dtype: object
province_state             
country_region    Venezuela
latitude             6.4238
longitude          -66.5897
report_date         4/13/20
total                   189
category          confirmed
Name: 227, dtype: object
province_state             
country_region      Vietnam
latitude                 16
longitude               108
report_date         4/13/20
total                   265
category          confirmed
Name: 228, dtype: object
province_state             
country_region       Zambia
latitude           -15.4167
longitude           28.28

province_state             
country_region     Barbados
latitude            13.1939
longitude          -59.5432
report_date         4/14/20
total                    72
category          confirmed
Name: 21, dtype: object
province_state             
country_region      Belarus
latitude            53.7098
longitude           27.9534
report_date         4/14/20
total                  3281
category          confirmed
Name: 22, dtype: object
province_state             
country_region      Belgium
latitude            50.8333
longitude                 4
report_date         4/14/20
total                 31119
category          confirmed
Name: 23, dtype: object
province_state             
country_region        Benin
latitude             9.3077
longitude            2.3158
report_date         4/14/20
total                    35
category          confirmed
Name: 24, dtype: object
province_state             
country_region       Bhutan
latitude            27.5142
longitude           90.4336
report_d

KeyboardInterrupt: 

In [99]:
db_connection.commit()

In [110]:

isTimeSeriesFirstExecution = True
while True:
    #**************** Start of Fetching Timeseries Report *********************#
    
    if isTimeSeriesFirstExecution == True:
        # delete existing data in the table
        cursor.execute("DELETE FROM covid_timeseries_report")
        # Saving the changes
        db_connection.commit()

    category = ['confirmed','deaths','recovered']
    for cat in category:
        print("Pulling data from server - " + cat)
            #"https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv
        url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_"+cat+"_global.csv"
        s=requests.get(url).content
        df_conf=pd.read_csv(io.StringIO(s.decode('utf-8')))
        df_conf = df_conf.rename(columns={
            "Province/State": "province_state",
            "Country/Region": "country_region",
            "Lat": "latitude",
            "Long": "longitude"
        })
        df_conf = df_conf.fillna('')
        
        df_conf.to_csv('time_series_19-covid-'+cat+'.csv',sep=',', encoding='utf-8', index=False)
        
        # Getting all the dates as list
        dates_col_list = df_conf.columns[4:len(df_conf.columns)]
        
        if isTimeSeriesFirstExecution == False:
            dates_col = [dates_col_list[::-1][0]]
        else:
            dates_col = dates_col_list
        print(dates_col)
        
        df_datewise= df_conf[['province_state', 'country_region', 'latitude', 'longitude']].copy()

        
        if isTimeSeriesFirstExecution == False:
            count_query = """select * from covid_timeseries_report where report_date = '"""+dates_col[0]+"""'
                          and category = '"""+cat+"""'"""
            print(count_query)
            cursor.execute(count_query)
            
            print("The number of records: ", cursor.rowcount)
            if cursor.rowcount > 1:
                dates_col = []
        
        if len(dates_col) > 0:
            print("Started inserting data to DB - " + cat)

            for d in dates_col:
                lst_count = list(df_conf[[d][0]])
                lst_same_date = [list(df_conf[[d]])[0] for i in range(len(lst_count))]
                lst_data_type = [cat for i in range(len(lst_count))]
                df_datewise['report_date'] = lst_same_date
                df_datewise['total'] = lst_count
                df_datewise['category'] = lst_data_type

                #print(df_datewise)

                # Inserting data to database datewise 
                # Inserting each row
                for row in df_datewise.iterrows():
                    #print(row[1])
                    province_state = row[1]['province_state']
                    country_region = row[1]['country_region']

                    # Incase the 's is present in the string it adds an escape character i.e. ''
                    if(province_state != ''):
                        province_state = province_state.replace("'","''")
                    if(country_region != ''):
                        country_region = country_region.replace("'","''")

                    query = """
                    INSERT into covid_timeseries_report(province_state, 
                        country_region, latitude, longitude,
                        report_date, total, category) 
                    values('%s','%s',%s,%s,'%s',%s,'%s');
                    """ % (province_state, country_region,
                           row[1]['latitude'], row[1]['longitude'],
                          row[1]['report_date'], row[1]['total'], row[1]['category'])
                    cursor.execute(query)
            print("Ended inserting data to DB - " + cat)
        else:
            print("Record already present for date "+dates_col_list[::-1][0]+" - " + cat)

        db_connection.commit()
    isTimeSeriesFirstExecution = False
    
    #**************** End of Fetching Timeseries Report *********************#

    # Sleep for 1 day; COVID19 data gets updated on daily basis
    now = datetime.now()
    timedate = ( (str(now.now())).split('.')[0]).split(' ')[0] + ' ' + ((str(now.now())).split('.')[0]).split(' ')[1]
 
    print(timedate, ' : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...')
    time.sleep(30)    
    continue

Pulling data from server - confirmed
Index(['1/22/20', '1/23/20', '1/24/20', '1/25/20', '1/26/20', '1/27/20',
       '1/28/20', '1/29/20', '1/30/20', '1/31/20', '2/1/20', '2/2/20',
       '2/3/20', '2/4/20', '2/5/20', '2/6/20', '2/7/20', '2/8/20', '2/9/20',
       '2/10/20', '2/11/20', '2/12/20', '2/13/20', '2/14/20', '2/15/20',
       '2/16/20', '2/17/20', '2/18/20', '2/19/20', '2/20/20', '2/21/20',
       '2/22/20', '2/23/20', '2/24/20', '2/25/20', '2/26/20', '2/27/20',
       '2/28/20', '2/29/20', '3/1/20', '3/2/20', '3/3/20', '3/4/20', '3/5/20',
       '3/6/20', '3/7/20', '3/8/20', '3/9/20', '3/10/20', '3/11/20', '3/12/20',
       '3/13/20', '3/14/20', '3/15/20', '3/16/20', '3/17/20', '3/18/20',
       '3/19/20', '3/20/20', '3/21/20', '3/22/20', '3/23/20', '3/24/20',
       '3/25/20', '3/26/20', '3/27/20', '3/28/20', '3/29/20', '3/30/20',
       '3/31/20', '4/1/20', '4/2/20', '4/3/20', '4/4/20', '4/5/20', '4/6/20',
       '4/7/20', '4/8/20', '4/9/20', '4/10/20', '4/11/20', '4/12/20

Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/18/20 - confirmed
Pulling data from server - deaths
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/18/20 - deaths
Pulling data from server - recovered
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/18/20 - recovered
2020-04-19 18:35:55  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and categor

Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/18/20 - confirmed
Pulling data from server - deaths
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/18/20 - deaths
Pulling data from server - recovered
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/18/20 - recovered
2020-04-19 18:41:01  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and categor

Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/18/20 - confirmed
Pulling data from server - deaths
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/18/20 - deaths
Pulling data from server - recovered
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/18/20 - recovered
2020-04-19 18:46:07  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and categor

Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/18/20 - confirmed
Pulling data from server - deaths
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/18/20 - deaths
Pulling data from server - recovered
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/18/20 - recovered
2020-04-19 18:51:14  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/18/20']
select * from covid_timeseries_report where report_date = '4/18/20'
                          and categor

...

Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/19/20 - confirmed
Pulling data from server - deaths
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/19/20 - deaths
Pulling data from server - recovered
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/19/20 - recovered
2020-04-19 20:23:15  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and categor

Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/19/20 - confirmed
Pulling data from server - deaths
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/19/20 - deaths
Pulling data from server - recovered
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/19/20 - recovered
2020-04-19 20:28:24  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and categor

Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/19/20 - confirmed
Pulling data from server - deaths
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/19/20 - deaths
Pulling data from server - recovered
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/19/20 - recovered
2020-04-19 20:33:30  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and categor

Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'confirmed'
The number of records:  264
Record already present for date 4/19/20 - confirmed
Pulling data from server - deaths
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'deaths'
The number of records:  264
Record already present for date 4/19/20 - deaths
Pulling data from server - recovered
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and category = 'recovered'
The number of records:  250
Record already present for date 4/19/20 - recovered
2020-04-19 20:38:36  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - confirmed
['4/19/20']
select * from covid_timeseries_report where report_date = '4/19/20'
                          and categor

ConnectionError: HTTPSConnectionPool(host='raw.githubusercontent.com', port=443): Max retries exceeded with url: /CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x120470710>: Failed to establish a new connection: [Errno 60] Operation timed out'))

### Pulling COVID-19 Realtime Data ( Daily World Report, Daily US Report and Timeseries Report)

In [ ]:

isTimeSeriesFirstExecution = True
while True:
    
    #**************** Start of Fetching Daily Report *********************#
    #utc_datetime = datetime.utcnow()-timedelta(days=1)
    #dt = utc_datetime.strftime("%m-%d-%Y")
    #
    #print("Pulling data from server - Daily Report")
    #url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/"+dt+".csv"
    #s=requests.get(url).content
    #df=pd.read_csv(io.StringIO(s.decode('utf-8')))
    #df = df.rename(columns={
    #    "Province_State": "province_state",
    #    "Country_Region": "country_region",
    #    "Last_Update": "last_updated",
    #    "Confirmed": "confirmed",
    #    "Deaths": "deaths",
    #    "Recovered": "recovered",
    #    "Lat": "latitude",
    #    "Long_": "longitude"
    #})
    #df.drop(columns=['FIPS', 'Admin2', 'Active', 'Combined_Key'])
    #df = df.fillna('')
    #df.to_csv('covid_19_report_'+dt+'.csv',sep=',', encoding='utf-8', index=False)
    #
    ## delete existing data in the table
    #cursor.execute("DELETE FROM covid_daily_report")
    ## Saving the changes
    #db_connection.commit()
    #
    #print("Started inserting data to DB - Daily Report")
    ## Inserting each row
    #for row in df.iterrows():
    #    province_state = row[1]['province_state']
    #    country_region = row[1]['country_region']
    #    latitude = row[1]['latitude']
    #    longitude = row[1]['longitude']
#
    #    # Incase the 's is present in the string it adds an escape character i.e. ''
    #    if(province_state != ''):
    #        province_state = province_state.replace("'","''")
    #    if(country_region != ''):
    #        country_region = country_region.replace("'","''")
    #    if(latitude == ''):
    #        latitude = 0.0
    #    if(longitude == ''):
    #        longitude = 0.0
    #    
#
    #    query = """
    #    INSERT into covid_daily_report(province_state, country_region,
    #    last_updated, confirmed,deaths, recovered, latitude, longitude) 
    #    values('%s','%s',TIMESTAMP '%s',%s,%s,%s,%s,%s);
    #    """ % (province_state, country_region,
    #           datetime.fromisoformat(row[1]['last_updated']),
    #          row[1]['confirmed'], row[1]['deaths'], row[1]['recovered'],
    #          latitude, longitude)
    #    cursor.execute(query)
    #
    #print("Ended inserting data to DB - Daily Report")
    ## Close the connection - Saving the changes
    #db_connection.commit()
    #
    
    utc_datetime = datetime.utcnow()-timedelta(days=1)
    dt = utc_datetime.strftime("%m-%d-%Y")
    
    print("Pulling data from server - Daily Report")
    url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/"+dt+".csv"
    s=requests.get(url).content
    df=pd.read_csv(io.StringIO(s.decode('utf-8')))
    df = df.fillna('')
    df.to_csv('covid_19_report_'+dt+'.csv',sep=',', encoding='utf-8', index=False)
    
    # delete existing data in the table
    cursor.execute("DELETE FROM covid_daily_report")
    # Saving the changes
    db_connection.commit()
    
    print("Started inserting data to DB - Daily Report")
    # Inserting each row
    for row in df.iterrows():
        fips = row[1]['FIPS']
        admin2 = row[1]['Admin2']
        province_state = row[1]['Province_State']
        country_region = row[1]['Country_Region']
        last_updated = row[1]['Last_Update']
        latitude = row[1]['Lat']
        longitude = row[1]['Long_']
        confirmed = row[1]['Confirmed']
        deaths = row[1]['Deaths']
        recovered = row[1]['Recovered']
        active = row[1]['Active']
        combined_key = row[1]['Combined_Key']

        # Incase the 's is present in the string it adds an escape character i.e. ''
        if(admin2 != ''):
            admin2 = admin2.replace("'","''")
        if(province_state != ''):
            province_state = province_state.replace("'","''")
        if(country_region != ''):
            country_region = country_region.replace("'","''")
        if(latitude == ''):
            latitude = 0.0
        if(longitude == ''):
            longitude = 0.0
        if(combined_key != ''):
            combined_key = combined_key.replace("'","''")
        

        query = """
        INSERT into covid_daily_report 
        values('%s','%s','%s','%s',TIMESTAMP '%s',
                %s,%s,%s,%s,%s,%s, '%s');
        """ % (fips, admin2, province_state, country_region, datetime.fromisoformat(last_updated),
              latitude, longitude, confirmed, deaths, recovered, active, combined_key)
        #print(query)
        cursor.execute(query)
    
    print("Ended inserting data to DB - Daily Report")
    # Close the connection - Saving the changes
    db_connection.commit()
    
    #**************** End of Fetching Daily Report *********************#
    
    
    #**************** Start of Fetching US Daily Report *********************#
    #utc_datetime = datetime.utcnow()-timedelta(days=1)
    #dt = utc_datetime.strftime("%m-%d-%Y")
#
    #print("Pulling data from server - US Daily Report")
    #url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports_us/"+dt+".csv"
    #s=requests.get(url).content
    #df=pd.read_csv(io.StringIO(s.decode('utf-8')))
    #df = df.rename(columns={
    #    "Province_State": "province_state",
    #    "Country_Region": "country_region",
    #    "Last_Update": "last_updated",
    #    "Confirmed": "confirmed",
    #    "Deaths": "deaths",
    #    "Recovered": "recovered",
    #    "Active": "active",
    #    "People_Tested": "people_tested",
    #    "People_Hospitalized": "people_hospitalized",
    #    "Lat": "latitude",
    #    "Long_": "longitude"
    #})
    #df.drop(columns=['FIPS', 'Incident_Rate', 'Mortality_Rate', 'UID', 'ISO3', 'Testing_Rate', 'Hospitalization_Rate'])
    #df = df.fillna('')
    #df.to_csv('covid_19_report_us_'+dt+'.csv',sep=',', encoding='utf-8', index=False)
#
    ## delete existing data in the table
    #cursor.execute("DELETE FROM covid_daily_report_us")
    ## Saving the changes
    #db_connection.commit()
#
    #print("Started inserting data to DB - US Daily Report")
    ## Inserting each row
    #for row in df.iterrows():
    #    province_state = row[1]['province_state']
    #    country_region = row[1]['country_region']
    #    latitude = row[1]['latitude']
    #    longitude = row[1]['longitude']
    #    confirmed = row[1]['confirmed']
    #    deaths = row[1]['deaths']
    #    recovered = row[1]['recovered']
    #    active = row[1]['active']
    #    people_tested = row[1]['people_tested']
    #    people_hospitalized = row[1]['people_hospitalized']
#
    #    # Incase the 's is present in the string it adds an escape character i.e. ''
    #    if(province_state != ''):
    #        province_state = province_state.replace("'","''")
    #    if(country_region != ''):
    #        country_region = country_region.replace("'","''")
    #    if(latitude == ''):
    #        latitude = 0.0
    #    if(longitude == ''):
    #        longitude = 0.0
    #    if(confirmed == ''):
    #        confirmed = 0
    #    if(deaths == ''):
    #        deaths = 0
    #    if(recovered == ''):
    #        recovered = 0
    #    if(active == ''):
    #        active = 0
    #    if(people_tested == ''):
    #        people_tested = 0
    #    if(people_hospitalized == ''):
    #        people_hospitalized = 0
#
#
#
    #    query = """
    #    INSERT into covid_daily_report_us(province_state, country_region,
    #    last_updated, confirmed,deaths, recovered,active,
    #    people_tested,people_hospitalized,latitude, longitude) 
    #    values('%s','%s','%s',%s,%s,%s,%s,%s,%s,%s,%s);
    #    """ % (province_state, country_region,
    #           row[1]['last_updated'],
    #          confirmed, deaths, recovered,active,
    #          people_tested,people_hospitalized,
    #          latitude, longitude)
    #    cursor.execute(query)
#
    #print("Ended inserting data to DB - US Daily Report")
    ## Close the connection - Saving the changes
    #db_connection.commit()

    utc_datetime = datetime.utcnow()-timedelta(days=1)
    dt = utc_datetime.strftime("%m-%d-%Y")

    print("Pulling data from server - US Daily Report")
    url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports_us/"+dt+".csv"
    s=requests.get(url).content
    df=pd.read_csv(io.StringIO(s.decode('utf-8')))
    df = df.fillna('')
    df.to_csv('covid_19_report_us_'+dt+'.csv',sep=',', encoding='utf-8', index=False)

    # delete existing data in the table
    cursor.execute("DELETE FROM covid_daily_report_us")
    # Saving the changes
    db_connection.commit()

    print("Started inserting data to DB - US Daily Report")
    # Inserting each row
    for row in df.iterrows():
        province_state = row[1]['Province_State']
        country_region = row[1]['Country_Region']
        last_updated = row[1]['Last_Update']
        latitude = row[1]['Lat']
        longitude = row[1]['Long_']
        confirmed = row[1]['Confirmed']
        deaths = row[1]['Deaths']
        recovered = row[1]['Recovered']
        active = row[1]['Active']
        fips = row[1]['FIPS']
        incident_rate  = row[1]['Incident_Rate']
        people_tested = row[1]['People_Tested']
        people_hospitalized = row[1]['People_Hospitalized']
        mortality_rate  = row[1]['Mortality_Rate']
        uid  = row[1]['UID']
        iso3  = row[1]['ISO3']
        testing_rate  = row[1]['Testing_Rate']
        hospitalization_rate  = row[1]['Hospitalization_Rate']

        # Incase the 's is present in the string it adds an escape character i.e. ''
        if(province_state != ''):
            province_state = province_state.replace("'","''")
        if(country_region != ''):
            country_region = country_region.replace("'","''")
        if(latitude == ''):
            latitude = 0.0
        if(longitude == ''):
            longitude = 0.0
        if(confirmed == ''):
            confirmed = 0
        if(deaths == ''):
            deaths = 0
        if(recovered == ''):
            recovered = 0
        if(active == ''):
            active = 0
        if(fips == ''):
            fips = ''
        if(people_tested == ''):
            people_tested = 0
        if(people_hospitalized == ''):
            people_hospitalized = 0
        if(incident_rate == ''):
            incident_rate = 0.0
        if(mortality_rate == ''):
            mortality_rate = 0.0
        if(uid == ''):
            uid = 0
        if(iso3 == ''):
            iso3 = 0
        if(testing_rate == ''):
            testing_rate = 0.0
        if(hospitalization_rate == ''):
            hospitalization_rate = 0.0



        query = """
        INSERT into covid_daily_report_us
        values('%s','%s','%s',%s,%s,
                %s,%s,%s,%s,'%s',
                %s,%s,%s,%s,'%s',
                '%s',%s,%s);
        """ % (province_state, country_region,last_updated,latitude, longitude,
              confirmed, deaths, recovered,active,fips,
              incident_rate, people_tested,people_hospitalized,mortality_rate, uid,
              iso3, testing_rate, hospitalization_rate)
        #print(query)
        cursor.execute(query)

    print("Ended inserting data to DB - US Daily Report")
    # Close the connection - Saving the changes
    db_connection.commit()
    
    #**************** End of Fetching US Daily Report *********************#
    
    
    #**************** Start of Fetching Timeseries Report *********************#
    
    # # delete existing data in the table
    #cursor.execute("DELETE FROM covid_timeseries_report")
    ## Saving the changes
    #db_connection.commit()
    #category = ['confirmed','deaths','recovered']
    #for cat in category:
    #    print("Pulling data from server - " + cat)
    #        #"https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv
    #    url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_"+cat+"_global.csv"
    #    s=requests.get(url).content
    #    df_conf=pd.read_csv(io.StringIO(s.decode('utf-8')))
    #    df_conf = df_conf.rename(columns={
    #        "Province/State": "province_state",
    #        "Country/Region": "country_region",
    #        "Lat": "latitude",
    #        "Long": "longitude"
    #    })
    #    df_conf = df_conf.fillna('')
    #    
    #    df_conf.to_csv('time_series_19-covid-'+cat+'.csv',sep=',', encoding='utf-8', index=False)
    #    
    #    # Getting all the dates as list
    #    dates_col = df_conf.columns[4:len(df_conf.columns)]
#
    #    df_datewise= df_conf[['province_state', 'country_region', 'latitude', 'longitude']].copy()
#
    #    print("Started inserting data to DB - " + cat)
    #    for d in dates_col:
    #        lst_count = list(df_conf[[d][0]])
    #        lst_same_date = [list(df_conf[[d]])[0] for i in range(len(lst_count))]
    #        lst_data_type = [cat for i in range(len(lst_count))]
    #        df_datewise['report_date'] = lst_same_date
    #        df_datewise['total'] = lst_count
    #        df_datewise['category'] = lst_data_type
#
    #        # Inserting data to database datewise 
    #        # Inserting each row
    #        for row in df_datewise.iterrows():
    #            #print(row[1])
    #            province_state = row[1]['province_state']
    #            country_region = row[1]['country_region']
#
    #            # Incase the 's is present in the string it adds an escape character i.e. ''
    #            if(province_state != ''):
    #                province_state = province_state.replace("'","''")
    #            if(country_region != ''):
    #                country_region = country_region.replace("'","''")
#
    #            query = """
    #            INSERT into covid_timeseries_report(province_state, 
    #                country_region, latitude, longitude,
    #                report_date, total, category) 
    #            values('%s','%s',%s,%s,'%s',%s,'%s');
    #            """ % (province_state, country_region,
    #                   row[1]['latitude'], row[1]['longitude'],
    #                  row[1]['report_date'], row[1]['total'], row[1]['category'])
    #            cursor.execute(query)
    #    print("Ended inserting data to DB - " + cat)
#
    #    db_connection.commit()
    
    
    if isTimeSeriesFirstExecution == True: # Executing it for first Time
        # delete existing data in the table
        cursor.execute("DELETE FROM covid_timeseries_report")
        # Saving the changes
        db_connection.commit()

    category = ['confirmed','deaths','recovered']
    for cat in category:
        print("Pulling data from server - " + cat)
            #"https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv
        url="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_"+cat+"_global.csv"
        s=requests.get(url).content
        df_conf=pd.read_csv(io.StringIO(s.decode('utf-8')))
        df_conf = df_conf.rename(columns={
            "Province/State": "province_state",
            "Country/Region": "country_region",
            "Lat": "latitude",
            "Long": "longitude"
        })
        df_conf = df_conf.fillna('')
        
        df_conf.to_csv('time_series_19-covid-'+cat+'.csv',sep=',', encoding='utf-8', index=False)
        
        # Getting all the dates as list
        dates_col_list = df_conf.columns[4:len(df_conf.columns)]
        
        if isTimeSeriesFirstExecution == False:
            dates_col = [dates_col_list[::-1][0]]
        else:
            dates_col = dates_col_list
        
        df_datewise= df_conf[['province_state', 'country_region', 'latitude', 'longitude']].copy()

        
        if isTimeSeriesFirstExecution == False:
            count_query = """select * from covid_timeseries_report where report_date = '"""+dates_col[0]+"""'
                          and category = '"""+cat+"""'"""
            cursor.execute(count_query)
            
            print("The number of records: ", cursor.rowcount)
            if cursor.rowcount > 1:
                dates_col = []
        
        if len(dates_col) > 0:
            print("Started inserting data to DB - " + cat)

            for d in dates_col:
                lst_count = list(df_conf[[d][0]])
                lst_same_date = [list(df_conf[[d]])[0] for i in range(len(lst_count))]
                lst_data_type = [cat for i in range(len(lst_count))]
                df_datewise['report_date'] = lst_same_date
                df_datewise['total'] = lst_count
                df_datewise['category'] = lst_data_type

                #print(df_datewise)

                # Inserting data to database datewise 
                # Inserting each row
                for row in df_datewise.iterrows():
                    #print(row[1])
                    province_state = row[1]['province_state']
                    country_region = row[1]['country_region']

                    # Incase the 's is present in the string it adds an escape character i.e. ''
                    if(province_state != ''):
                        province_state = province_state.replace("'","''")
                    if(country_region != ''):
                        country_region = country_region.replace("'","''")

                    query = """
                    INSERT into covid_timeseries_report(province_state, 
                        country_region, latitude, longitude,
                        report_date, total, category) 
                    values('%s','%s',%s,%s,'%s',%s,'%s');
                    """ % (province_state, country_region,
                           row[1]['latitude'], row[1]['longitude'],
                          row[1]['report_date'], row[1]['total'], row[1]['category'])
                    cursor.execute(query)
            print("Ended inserting data to DB - " + cat)
        else:
            print("Record already present for date "+dates_col_list[::-1][0]+" - " + cat)

        db_connection.commit()
    isTimeSeriesFirstExecution = False
    
    #**************** End of Fetching Timeseries Report *********************#
    
    # Sleep for 1 day; COVID19 data gets updated on daily basis
    now = datetime.now()
    timedate = ( (str(now.now())).split('.')[0]).split(' ')[0] + ' ' + ((str(now.now())).split('.')[0]).split(' ')[1]
 
    print(timedate, ' : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...')
    time.sleep(24*60*60)    
    continue


Pulling data from server - Daily Report
Started inserting data to DB - Daily Report
Ended inserting data to DB - Daily Report
Pulling data from server - US Daily Report
Started inserting data to DB - US Daily Report
Ended inserting data to DB - US Daily Report
Pulling data from server - confirmed
Started inserting data to DB - confirmed
Ended inserting data to DB - confirmed
Pulling data from server - deaths
Started inserting data to DB - deaths
Ended inserting data to DB - deaths
Pulling data from server - recovered
Started inserting data to DB - recovered
Ended inserting data to DB - recovered
2020-04-19 21:35:45  : Fetched data from GIT for Covid Daily Report and Going to sleep for 1-day now ...
Pulling data from server - Daily Report
Started inserting data to DB - Daily Report
Ended inserting data to DB - Daily Report
Pulling data from server - US Daily Report
Started inserting data to DB - US Daily Report
Ended inserting data to DB - US Daily Report
Pulling data from server - conf